# Tensorflow 实现cnn代码
本文代码是[使用Tensorflow构建cnn系统完成mnist data识别](https://www.tensorflow.org/tutorials/layers)教程的部分代码。

In [1]:
from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

# Imports
import numpy as np
import tensorflow as tf

tf.logging.set_verbosity(tf.logging.INFO)

In [2]:
def cnn_model_fn(features, labels, mode):
    """Model function for CNN."""
    '''
    函数中包含训练、测试、预测等实现方法，函数cnn_model_fn相当于勾勒了一幅计算图
    '''
    # Input Layer
    input_layer = tf.reshape(features["x"], [-1, 28, 28, 1])

    # Convolutional Layer #1
    conv1 = tf.layers.conv2d(
        inputs=input_layer,
        filters=32,
        kernel_size=[5, 5],
        padding="same",
        activation=tf.nn.relu)

    # Pooling Layer #1
    pool1 = tf.layers.max_pooling2d(inputs=conv1, pool_size=[2, 2], strides=2)

    # Convolutional Layer #2 and Pooling Layer #2
    conv2 = tf.layers.conv2d(
        inputs=pool1,
        filters=64,
        kernel_size=[5, 5],
        padding="same",
        activation=tf.nn.relu)
    pool2 = tf.layers.max_pooling2d(inputs=conv2, pool_size=[2, 2], strides=2)

    # Dense Layer
    pool2_flat = tf.reshape(pool2, [-1, 7 * 7 * 64])
    dense = tf.layers.dense(inputs=pool2_flat, units=1024, activation=tf.nn.relu)
    dropout = tf.layers.dropout(
      inputs=dense, rate=0.4, training=mode == tf.estimator.ModeKeys.TRAIN)

    # Logits Layer
    logits = tf.layers.dense(inputs=dropout, units=10)

    predictions = {
      # Generate predictions (for PREDICT and EVAL mode)
      "classes": tf.argmax(input=logits, axis=1),
      # Add `softmax_tensor` to the graph. It is used for PREDICT and by the
      # `logging_hook`.
      "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
  }

    if mode == tf.estimator.ModeKeys.PREDICT:
        return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)

    # Calculate Loss (for both TRAIN and EVAL modes)
    loss = tf.losses.sparse_softmax_cross_entropy(labels=labels, logits=logits)

    # Configure the Training Op (for TRAIN mode)
    if mode == tf.estimator.ModeKeys.TRAIN:
        optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
        train_op = optimizer.minimize(
        loss=loss,
        global_step=tf.train.get_global_step())
        return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)

    # Add evaluation metrics (for EVAL mode)
    eval_metric_ops = {
      "accuracy": tf.metrics.accuracy(
          labels=labels, predictions=predictions["classes"])}
    return tf.estimator.EstimatorSpec(
      mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)


## 输入数据

In [3]:
mnist = tf.contrib.learn.datasets.load_dataset('mnist')

Successfully downloaded train-images-idx3-ubyte.gz 9912422 bytes.
Extracting MNIST-data/train-images-idx3-ubyte.gz
Successfully downloaded train-labels-idx1-ubyte.gz 28881 bytes.
Extracting MNIST-data/train-labels-idx1-ubyte.gz
Successfully downloaded t10k-images-idx3-ubyte.gz 1648877 bytes.
Extracting MNIST-data/t10k-images-idx3-ubyte.gz
Successfully downloaded t10k-labels-idx1-ubyte.gz 4542 bytes.
Extracting MNIST-data/t10k-labels-idx1-ubyte.gz


In [4]:
train_data = mnist.train.images  #returns np.array
#修改labels数值类型，从int8修改成int32
train_labels = np.asarray(mnist.train.labels,dtype=np.int32) 
eval_data = mnist.test.images
#修改labels数值类型，从int8修改成int32
eval_labels = np.array(mnist.test.labels,dtype=np.int32)

In [13]:
mnist_classifier = tf.estimator.Estimator(
    model_fn = cnn_model_fn,model_dir='./tmp/mnist_convnet_model')

INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_save_checkpoints_secs': 600, '_session_config': None, '_keep_checkpoint_max': 5, '_task_type': 'worker', '_is_chief': True, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x7fd46c1dcdd0>, '_save_checkpoints_steps': None, '_keep_checkpoint_every_n_hours': 10000, '_service': None, '_num_ps_replicas': 0, '_tf_random_seed': None, '_master': '', '_num_worker_replicas': 1, '_task_id': 0, '_log_step_count_steps': 100, '_model_dir': './tmp/mnist_convnet_model', '_save_summary_steps': 100}


In [14]:
# Set up logging for predictions
tensors_to_log = {"probabilities": "softmax_tensor"}
logging_hook = tf.train.LoggingTensorHook(tensors=tensors_to_log, every_n_iter=50)

In [15]:
# Train the model
train_input_fn = tf.estimator.inputs.numpy_input_fn(
    x={"x": train_data},
    y=train_labels,
    batch_size=100,   #定义批次训练数据数量
    num_epochs=None,
    shuffle=True)
mnist_classifier.train(
    input_fn=train_input_fn,
    steps=20000,
    hooks=[logging_hook])

INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Saving checkpoints for 1 into ./tmp/mnist_convnet_model/model.ckpt.
INFO:tensorflow:probabilities = [[0.09410633 0.09824092 0.09193816 0.10422927 0.10371997 0.10964907
  0.09979954 0.10699821 0.09989516 0.09142339]
 [0.08950403 0.11422057 0.0929253  0.1104778  0.10297372 0.10545325
  0.09434819 0.09494788 0.095113   0.10003626]
 [0.0849553  0.11236744 0.09137576 0.1095414  0.12767695 0.10228337
  0.08013968 0.09579895 0.09612555 0.09973557]
 [0.09336904 0.10262905 0.09757156 0.09847476 0.10257956 0.10633713
  0.09864542 0.09797096 0.10287874 0.09954372]
 [0.09899634 0.10330457 0.07919297 0.09496624 0.10444247 0.11481661
  0.09665501 0.10649195 0.0908989  0.11023492]
 [0.1051648  0.10973919 0.09848446 0.10943635 0.10343346 0.09088334
  0.08614041 0.10374936 0.10073221 0.09223644]
 [0.10150953 0.10886008 0.09703594 0.10518607 0.10451692 0.10236294
  0.08908001 0.10500868 0.09582095 0.09061897]
 [0.09614898 0.11209515 0.08566882 

INFO:tensorflow:loss = 2.301382, step = 1
INFO:tensorflow:probabilities = [[0.0946402  0.10560785 0.0970287  0.0991356  0.11011882 0.09369071
  0.09820371 0.10745124 0.09832934 0.09579386]
 [0.09934279 0.108544   0.0977928  0.11035327 0.0889678  0.10566705
  0.09833224 0.09831548 0.0923215  0.10036304]
 [0.0985935  0.11033555 0.09382937 0.10335097 0.11130689 0.10763025
  0.09851721 0.09905304 0.08923353 0.0881497 ]
 [0.09540913 0.10137255 0.09201729 0.10845421 0.10131168 0.10437937
  0.09801633 0.09915026 0.09405645 0.10583271]
 [0.09735218 0.10713675 0.09731458 0.1076933  0.10310962 0.0974235
  0.08919546 0.10804547 0.09739741 0.09533177]
 [0.09151439 0.10322514 0.08897967 0.10686785 0.10388065 0.11473299
  0.10144038 0.09309912 0.09431845 0.10194121]
 [0.09270824 0.10241047 0.08856747 0.11899703 0.09177794 0.10144593
  0.10028971 0.10483873 0.09827266 0.10069181]
 [0.09073871 0.10285963 0.10182965 0.10593177 0.10305882 0.10488127
  0.10258828 0.09601387 0.09721791 0.09488007]
 [0.101

INFO:tensorflow:global_step/sec: 10.3265
INFO:tensorflow:probabilities = [[0.0919562  0.09800757 0.10062163 0.10402524 0.09272658 0.10954498
  0.10071574 0.10372341 0.09969287 0.09898581]
 [0.09959572 0.10362412 0.09509064 0.10349292 0.09873599 0.10459826
  0.0984022  0.09747116 0.09914608 0.0998429 ]
 [0.09295736 0.11116448 0.09741895 0.10018406 0.10165463 0.10005502
  0.09686712 0.10505999 0.09646063 0.09817775]
 [0.09213335 0.10485203 0.09598742 0.10005997 0.1028768  0.09853135
  0.099659   0.10290781 0.0956953  0.10729697]
 [0.10471059 0.11582856 0.09393185 0.09679835 0.09367429 0.11010327
  0.09871501 0.08660749 0.09831367 0.10131692]
 [0.10478536 0.10114034 0.08965222 0.09774951 0.11434733 0.10925612
  0.10109713 0.09463435 0.10237654 0.08496113]
 [0.0999009  0.10586745 0.1010806  0.10517037 0.10067678 0.09725846
  0.09610616 0.11028244 0.09427463 0.08938222]
 [0.09036241 0.10052867 0.09728382 0.10124267 0.10591091 0.104038
  0.0980374  0.1069159  0.10300973 0.09267041]
 [0.09652

INFO:tensorflow:loss = 2.299261, step = 101 (9.683 sec)
INFO:tensorflow:probabilities = [[0.0918917  0.10059628 0.09974635 0.12156951 0.10066611 0.10272074
  0.08924038 0.09841526 0.09508487 0.1000689 ]
 [0.09659788 0.10919704 0.0963836  0.11864271 0.09269069 0.09383522
  0.09901991 0.10480236 0.10550495 0.08332568]
 [0.08863696 0.1110777  0.10328631 0.10909335 0.10558387 0.09540947
  0.09544338 0.09951305 0.09521338 0.0967425 ]
 [0.09651889 0.10136686 0.09453981 0.10841648 0.10274382 0.11741868
  0.09803866 0.09148118 0.10084543 0.08863027]
 [0.09422883 0.10578521 0.0862897  0.09641833 0.11025997 0.09790014
  0.0995323  0.09750067 0.10437211 0.10771281]
 [0.09131413 0.10219828 0.10023218 0.10846351 0.10909241 0.10410447
  0.09253439 0.10636519 0.09419154 0.09150387]
 [0.09671786 0.10139091 0.09436376 0.10015611 0.10529325 0.09918149
  0.10084604 0.10133943 0.09802908 0.10268203]
 [0.09698878 0.09807807 0.10868171 0.09779731 0.09696431 0.09672762
  0.09382401 0.1065451  0.09776758 0.10

INFO:tensorflow:global_step/sec: 10.4172
INFO:tensorflow:probabilities = [[0.10220324 0.1150215  0.09207015 0.11433345 0.08800224 0.09627938
  0.08897465 0.09454547 0.09983399 0.10873594]
 [0.09330083 0.09775823 0.09630573 0.11045998 0.10240053 0.10183079
  0.09907445 0.09857775 0.10056989 0.09972175]
 [0.08755349 0.09832045 0.09624349 0.09801064 0.09378165 0.09905106
  0.10801497 0.1081221  0.09713522 0.11376698]
 [0.09653571 0.1109444  0.09005095 0.10379308 0.10748414 0.10496014
  0.09330326 0.10454281 0.09291532 0.09547024]
 [0.1040919  0.10231005 0.10303301 0.10718382 0.1029985  0.1010304
  0.09134966 0.10096502 0.09625892 0.09077873]
 [0.09254903 0.10176752 0.10660667 0.09556248 0.09832928 0.09729291
  0.10663606 0.1044801  0.09706305 0.09971287]
 [0.10174734 0.10290813 0.11192559 0.10316008 0.10506664 0.09752692
  0.08928042 0.09618844 0.10264029 0.08955611]
 [0.09148507 0.10219093 0.09460837 0.10132518 0.09617984 0.10190867
  0.10736161 0.1021864  0.10122278 0.10153113]
 [0.0997

...

INFO:tensorflow:global_step/sec: 10.1964
INFO:tensorflow:probabilities = [[0.00000026 0.00000001 0.00001549 0.00007313 0.         0.00003506
  0.         0.00000003 0.999876   0.00000001]
 [0.00000131 0.00000021 0.00006331 0.9992155  0.00000011 0.00011108
  0.00000001 0.00000013 0.00054115 0.00006724]
 [0.00000078 0.0000093  0.00000901 0.01541725 0.00000624 0.00274383
  0.00000149 0.9815122  0.00001024 0.00028965]
 [0.00259835 0.9477493  0.00563061 0.00234992 0.00031712 0.00039861
  0.00487157 0.0010146  0.0349213  0.00014854]
 [0.00000539 0.00000152 0.00002784 0.00014143 0.02952623 0.05840193
  0.00000223 0.43522236 0.06447911 0.4121919 ]
 [0.00000022 0.00000001 0.00000006 0.0000668  0.         0.99992704
  0.0000014  0.         0.00000296 0.00000155]
 [0.00145962 0.00000051 0.00009303 0.00026048 0.00001484 0.00694757
  0.00000016 0.96540225 0.00052635 0.02529517]
 [0.00000011 0.00000029 0.000003   0.0000089  0.00066492 0.00001846
  0.00000018 0.00050282 0.0000261  0.9987752 ]
 [0.000

INFO:tensorflow:loss = 0.15988979, step = 19801 (9.807 sec)
INFO:tensorflow:probabilities = [[0.00001407 0.00000391 0.00000316 0.00002482 0.8569069  0.00951407
  0.00008195 0.0265813  0.00010542 0.10676442]
 [0.00384231 0.00197575 0.36810797 0.2817332  0.00041322 0.00043352
  0.00004379 0.28835863 0.01237285 0.04271875]
 [0.00004686 0.0000018  0.00028935 0.00000361 0.00062667 0.00002896
  0.9988927  0.00000044 0.00009606 0.00001362]
 [0.00002577 0.99522483 0.00021679 0.00003982 0.00061209 0.00000707
  0.00004682 0.001267   0.00249027 0.00006948]
 [0.00021366 0.00003163 0.01446043 0.91142905 0.00000351 0.00021155
  0.00000216 0.00004594 0.06553974 0.00806228]
 [0.00000053 0.00000684 0.00007911 0.00054084 0.00433962 0.00005912
  0.00000116 0.00099207 0.00259561 0.9913851 ]
 [0.99926084 0.0000001  0.00024294 0.00000254 0.00001659 0.00005257
  0.00002769 0.00001519 0.0001201  0.00026149]
 [0.00029647 0.00000026 0.99822944 0.00135047 0.00000017 0.00010642
  0.00000112 0.0000003  0.00001514 

INFO:tensorflow:global_step/sec: 10.2462
INFO:tensorflow:probabilities = [[0.0000006  0.00005314 0.00057505 0.00109857 0.00030229 0.00040196
  0.00000207 0.27979606 0.00740903 0.71036124]
 [0.00000036 0.00000206 0.00000021 0.00000017 0.9975326  0.00016888
  0.00002228 0.00000509 0.0019043  0.00036401]
 [0.9802388  0.000005   0.00156838 0.00034383 0.00000012 0.01659545
  0.00051586 0.00001298 0.00050179 0.00021782]
 [0.00003969 0.00000134 0.0005862  0.0002125  0.00000987 0.00044215
  0.00000013 0.9671407  0.00160237 0.02996509]
 [0.08474159 0.00001485 0.88697505 0.02075752 0.00000416 0.00387282
  0.00019913 0.00037849 0.00111669 0.00193971]
 [0.00000001 0.00000233 0.00002456 0.00048045 0.01372619 0.00001929
  0.00000003 0.00153999 0.00032229 0.9838848 ]
 [0.00320634 0.02006731 0.01342945 0.05679447 0.00064185 0.05755036
  0.00342254 0.00097823 0.83786666 0.00604278]
 [0.00001574 0.00001764 0.00180546 0.00041573 0.9907973  0.0036387
  0.0004619  0.00022242 0.00018717 0.00243797]
 [0.0000

INFO:tensorflow:loss = 0.09993139, step = 19901 (9.760 sec)
INFO:tensorflow:probabilities = [[0.9983405  0.00000005 0.00003868 0.0000553  0.         0.00119011
  0.00000161 0.00027571 0.00005476 0.00004316]
 [0.00000162 0.0000022  0.0005839  0.96746695 0.00000004 0.00010765
  0.00000001 0.00009637 0.03101643 0.00072489]
 [0.00000412 0.00000745 0.00000244 0.00007036 0.00000425 0.999762
  0.00005548 0.00000101 0.0000873  0.00000565]
 [0.00063441 0.02697241 0.1421423  0.00064706 0.00716868 0.00221796
  0.8136963  0.00001689 0.00649374 0.00001024]
 [0.0000035  0.00000037 0.00005134 0.00000193 0.99969625 0.00000816
  0.00001127 0.00006368 0.00001025 0.00015332]
 [0.00140942 0.00000982 0.00290546 0.00583863 0.00114145 0.00520576
  0.00476756 0.00000132 0.97818005 0.00054063]
 [0.00000021 0.0000019  0.00000817 0.999918   0.00000002 0.00006115
  0.00000002 0.0000001  0.00000115 0.00000926]
 [0.00068219 0.96162635 0.0025626  0.00692549 0.00849282 0.00333992
  0.00199602 0.00573538 0.00599103 0.

INFO:tensorflow:Saving checkpoints for 20000 into ./tmp/mnist_convnet_model/model.ckpt.
INFO:tensorflow:Loss for final step: 0.06820124.


In [16]:
# Evaluate the model and print results
eval_input_fn = tf.estimator.inputs.numpy_input_fn(
    x={"x": eval_data},
    y=eval_labels,
    num_epochs=1,
    shuffle=False) #输入层input layer输入的数据和参数
eval_results = mnist_classifier.evaluate(input_fn=eval_input_fn)
print(eval_results)

INFO:tensorflow:Starting evaluation at 2018-03-08-03:59:26
INFO:tensorflow:Restoring parameters from ./tmp/mnist_convnet_model/model.ckpt-20000
INFO:tensorflow:Finished evaluation at 2018-03-08-03:59:29
INFO:tensorflow:Saving dict for global step 20000: accuracy = 0.9712, global_step = 20000, loss = 0.09779028
{'loss': 0.09779028, 'global_step': 20000, 'accuracy': 0.9712}
